# Clustering

This notebook will be investigating the proper clustering method based on the results from Feature_Selection notebook. This notebook show some potential that the dimension reduction by feature selection and PCA show some potential that this could have some potential even with visual clustering.
Therefore we will be investigating sophisticated method of clustering and it will improve based on this result.






In [88]:
import os
# Set the environment variable
os.environ['OMP_NUM_THREADS'] = '1'

import pandas as pd
from sklearn.mixture import GaussianMixture
import plotly.express as px
import matplotlib.pyplot as plt
import numpy as np
from sklearn.preprocessing import StandardScaler
import seaborn as sns


import matplotlib.pyplot as plt
import seaborn as sns
import random
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Load the data

In [89]:
# Read CSV files into DataFrames
df_mi_corr = pd.read_csv("../processed_data/lazy_corr_MI_10_FS.csv")
df_mi_corr_50 = pd.read_csv("../processed_data/lazy_corr_MI_50_FS.csv")
df_corr = pd.read_csv("../processed_data/lazy_corr_FS.csv")
df_mi = pd.read_csv("../processed_data/batch_corr_MI_10_FS.csv")
df = pd.read_csv("../processed_data/batch_corr_FS.csv")
df_mi_50= pd.read_csv("../processed_data/batch_corr_MI_50_FS.csv")


df_corr_scaled_mi_batch_50= pd.read_csv("../processed_data/batch_corr_batch_MI_50_FS.csv")

df_corr_scaled_nomiddle= pd.read_csv("../processed_data/batch_corr_MI_nomiddle_50_FS.csv")

df_corr_scaled_mi_nofreq_50= pd.read_csv("../processed_data/batch_corr_MI_nofreq_50_FS.csv")

First we will be investigating df_mi and df_mi_50 that had good visualization result using PCA. Following figures were the results:

<img src="Figures\MI-batch Correlation with top 10 features_2D.png" alt="sphx_glr_plot_cluster_comparison_001" width="1500"/>
<img src="Figures\MI-batch Correlation with top 10 features_3d.png" alt="sphx_glr_plot_cluster_comparison_001" width="1500"/>

Based on the analytics and the nature of the clustering method where we want to find anomalies Gaussian Mixture model will be first thing to be investigated. 

<img src="https://scikit-learn.org/stable/_images/sphx_glr_plot_cluster_comparison_001.png" alt="sphx_glr_plot_cluster_comparison_001" width="1200"/>


# Gaussian Mixture Model 

Gaussian Mixture Models (GMM) can be used for anomaly detection by identifying data points that do not fit well into any of the Gaussian distributions modeled by the GMM. These points are considered anomalies because they have a low probability of belonging to any of the clusters.



In [90]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.mixture import GaussianMixture
import plotly.express as px

def tune_gmm(data, n_components_range=range(1, 15), criterion='AIC'):
    """
    Perform hyperparameter tuning for a Gaussian Mixture Model (GMM),
    store the results in a DataFrame, visualize the results, and return the best model.

    Parameters:
    - data: pd.DataFrame - The input data for GMM clustering.
    - n_components_range: range - The range of number of components to try.
    - criterion: str - The criterion to use for selecting the best model ('AIC' or 'BIC').

    Returns:
    - best_model: GaussianMixture - The best GMM model based on the chosen criterion.
    - results_df: pd.DataFrame - The DataFrame containing AIC and BIC values for each model.
    """
    
    # Standardize the features
    scaler = StandardScaler()
    features_scaled = scaler.fit_transform(data)

    # Create lists to store the results
    aic_values = []
    bic_values = []
    n_components_list = []

    # Loop over the range of components
    for n_components in n_components_range:
        gmm = GaussianMixture(n_components=n_components, random_state=42)
        gmm.fit(features_scaled)
        
        aic = gmm.aic(features_scaled)
        bic = gmm.bic(features_scaled)
        
        aic_values.append(aic)
        bic_values.append(bic)
        n_components_list.append(n_components)

    # Create a DataFrame to store the results
    results_df = pd.DataFrame({
        'n_components': n_components_list,
        'AIC': aic_values,
        'BIC': bic_values
    })

    # Plot AIC and BIC values
    fig = px.line(results_df, x='n_components', y=['AIC', 'BIC'], 
                  title='AIC and BIC values for different number of components',
                  labels={'value': 'Score', 'n_components': 'Number of Components'},
                  markers=True)
    fig.show()

    # Find the best model based on the chosen criterion
    if criterion == 'AIC':
        best_index = results_df['AIC'].idxmin()
    elif criterion == 'BIC':
        best_index = results_df['BIC'].idxmin()
    else:
        raise ValueError("Criterion must be either 'AIC' or 'BIC'")

    best_model = GaussianMixture(n_components=results_df.loc[best_index, 'n_components'], random_state=42)
    best_model.fit(features_scaled)

    return best_model, results_df


In [91]:
best_gmm_model, tuning_results = tune_gmm(df_mi, n_components_range=range(1, 15), criterion='AIC')
print(best_gmm_model)

GaussianMixture(n_components=14, random_state=42)


Picked best number of component with elbow method and it is seems to be 6

## Perform Cluster

Bsaed on the elbow method we will be pick number of component that seems to be well performing.

In [92]:
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.mixture import GaussianMixture
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
import plotly.express as px

def train_GMM(df, n_components=5, random_state=42, visualization_method='PCA', plot_3d=False):
    """
    Train a Gaussian Mixture Model (GMM) on the given dataframe, predict clusters, and visualize the results.

    Parameters:
    df (DataFrame): The DataFrame containing the features to cluster.
    n_components (int): The number of clusters/components for the GMM.
    random_state (int): Random state for reproducibility.
    visualization_method (str): The method for visualization ('PCA' or 'TSNE').
    plot_3d (bool): Whether to generate a 3D plot. If False, a 2D plot will be generated.

    Returns:
    DataFrame: The original DataFrame with an additional column for cluster labels.
    GaussianMixture: The fitted GMM model.
    """

    # Standardize the features
    df = df.copy()
    sensor_ids = df.index if 'Sensor ID' not in df.columns else df['Sensor ID']
    scaler = StandardScaler()
    features_scaled = scaler.fit_transform(df.drop(columns=['Sensor ID']))

    # Fit a Gaussian Mixture Model
    gmm = GaussianMixture(n_components=n_components, random_state=random_state)
    gmm.fit(features_scaled)

    # Predict cluster labels
    cluster_labels = gmm.predict(features_scaled)
    df['cluster'] = cluster_labels

    print("============ Distribution of Sensors in each Cluster ============")
    print(df.groupby(["cluster"])["Sensor ID"].count())

    # Evaluate the model using BIC and AIC
    bic = gmm.bic(features_scaled)
    aic = gmm.aic(features_scaled)

    print(f"BIC: {bic}")
    print(f"AIC: {aic}")

    # Visualize the clustering results using PCA or t-SNE
    if visualization_method.upper() == 'PCA':
        n_components = 3 if plot_3d else 2
        pca = PCA(n_components=n_components)
        components = pca.fit_transform(features_scaled)
        title = '3D Visualization using PCA' if plot_3d else '2D Visualization using PCA'
    elif visualization_method.upper() == 'TSNE':
        n_components = 3 if plot_3d else 2
        tsne = TSNE(n_components=n_components, random_state=random_state)
        components = tsne.fit_transform(features_scaled)
        title = '3D Visualization using t-SNE' if plot_3d else '2D Visualization using t-SNE'
    else:
        raise ValueError("visualization_method should be either 'PCA' or 'TSNE'.")

    # Create a DataFrame for the components
    components_df = pd.DataFrame(components, columns=[f'Component {i+1}' for i in range(n_components)])
    components_df['cluster'] = cluster_labels
    components_df['Sensor ID'] = sensor_ids

    # Plot the results
    if plot_3d:
        fig = px.scatter_3d(
            components_df, 
            x='Component 1', 
            y='Component 2', 
            z='Component 3', 
            color='cluster', 
            title=title,
            hover_name='Sensor ID'  # Display Sensor ID on hover
        )
    else:
        fig = px.scatter(
            components_df, 
            x='Component 1', 
            y='Component 2', 
            color='cluster', 
            title=title,
            hover_name='Sensor ID'  # Display Sensor ID on hover
        )
    
    fig.show()

    return df, gmm

# Example usage:
# df, gmm = train_GMM(df, n_components=5, random_state=42, visualization_method='PCA', plot_3d=True)


## Evaluation Methods
One of the hard thing about the clustering is how to evaluate the clustering. To do so we will leverage the nature of our dataset.

weighted average of average variability of pingtime: This will reveals the how much variability within the cluster. This does not compare each cluster's quality and having more cluster is always better but this doesn't account that either.


In [93]:
# Load the dataset
file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
all_cleaned_df = pd.read_csv(file_path)
all_cleaned_df = all_cleaned_df.drop("Unnamed: 0",axis=1)

In [94]:
def identify_outliers(series):
    Q1 = series.quantile(0.25)
    Q3 = series.quantile(0.75)
    IQR = Q3 - Q1
    lower_bound = Q1 - 1.5 * IQR
    upper_bound = Q3 + 1.5 * IQR
    return ((series < lower_bound) | (series > upper_bound)).sum()

def average_variability_metrics(df_cluster, all_cleaned_df):
    """
    Calculate the average number of outliers and average standard deviation of ping time for each cluster,
    and the weighted averages of these values.

    Parameters:
    df_cluster (DataFrame): The DataFrame containing sensor ID and their respective clusters.
    all_cleaned_df (DataFrame): The DataFrame containing the cleaned data.

    Returns:
    DataFrame: A DataFrame with columns for cluster, average number of outliers, and average std ping time.
    float: The weighted average of the average number of outliers across clusters.
    float: The weighted average of the average standard deviation of ping time across clusters.
    """

    # List to store the results
    results = []

    # Iterate over each cluster
    for target in df_cluster["cluster"].unique():
        # Get the sensor IDs for the current cluster
        cluster_sensors = df_cluster[df_cluster["cluster"] == target]["Sensor ID"].unique()

        # Filter the all_cleaned_df for the current cluster sensors
        all_cleaned_df_target = all_cleaned_df[all_cleaned_df['Sensor ID'].isin(cluster_sensors)]

        # Group by 'Delay (us)' and 'Range (cm)', then calculate the number of outliers in 'Ping Time (us)'
        grouped_outliers = all_cleaned_df_target.groupby(['Delay (us)', 'Range (cm)'])['Ping Time (us)'].apply(identify_outliers).reset_index(name='outliers')
        
        # Calculate the average number of outliers for the current cluster
        avg_count_outliers = grouped_outliers['outliers'].mean()
        max_count_outliers = grouped_outliers['outliers'].max()

        # Group by sensor ID, delay, and range, then calculate the standard deviation of ping time
        grouped_std = all_cleaned_df_target.groupby(['Sensor ID', 'Delay (us)', 'Range (cm)']).agg(
            std_ping_time=('Ping Time (us)', 'std')
        ).reset_index()

        # Calculate the average std ping time for the current cluster
        avg_std_ping_time = grouped_std['std_ping_time'].mean()

        # Append the results to the list
        results.append({'cluster': target, 'max_count_outliers':max_count_outliers, 'avg_count_outliers': avg_count_outliers, 'avg_std_ping_time': avg_std_ping_time, 'count': len(cluster_sensors)})
    
    # Convert the results list to a DataFrame
    results_df = pd.DataFrame(results)
    
    # Calculate the weighted average of the average number of outliers

    results_df['weighted_avg_count_outliers'] =(results_df['max_count_outliers']-results_df['avg_count_outliers']) /results_df['count']
    weighted_avg_count_outliers_score = results_df['weighted_avg_count_outliers'].mean()

    # Calculate the weighted average of the average std ping time
    results_df['weighted_avg_std_ping_time'] = results_df['avg_std_ping_time'] /results_df['count']*(results_df['cluster']+1)
    weighted_avg_std_ping_time_score = results_df['weighted_avg_std_ping_time'].mean()

    return results_df, weighted_avg_count_outliers_score, weighted_avg_std_ping_time_score



In [95]:
df_mi_gmm_8,gmm_8 = train_GMM(df_mi, n_components=8, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0    151
1     17
2     20
3      1
4      1
5      1
6      1
7     18
Name: Sensor ID, dtype: int64
BIC: 728.021918808392
AIC: -1035.9037498797138


In [96]:
results_df, weighted_avg_outliers_score, weighted_avg_std_ping_time_score = average_variability_metrics(df_mi_gmm_8,all_cleaned_df)

results_df

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        7                 119           20.377778          19.304321     18   
1        0                1128          552.355556          47.569719    151   
2        6                  23            5.400000          26.583564      1   
3        2                 323           53.400000         305.171276     20   
4        1                 140           28.577778         619.375891     17   
5        4                  19            4.644444          13.420619      1   
6        5                  22            2.622222         380.734807      1   
7        3                  23            3.577778          16.225759      1   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     5.479012                    8.579698  
1                     3.812215                    0.315031  
2                    17.600000                  186.084948  
3                    13.480000                   45.775691  
4                     6.554248                   72.867752  
5                    14.355556                   67.103096  
6                    19.377778                 2284.408841  
7                    19.422222                   64.903037

Based on this evaluation method we can do gridsearch on the n_component and also performs elbow method.

In [97]:
def search_gmm_weighted_avg(df,data, n_components_range=range(2, 20)):
    for i in n_components_range:
        # Standardize the features
        scaler = StandardScaler()
        features_scaled = scaler.fit_transform(df)

        # Fit a Gaussian Mixture Model
        gmm = GaussianMixture(n_components=i, random_state=42)
        gmm.fit(features_scaled)

        # Predict cluster labels
        cluster_labels = gmm.predict(features_scaled)
        df['cluster'] = cluster_labels
        
        results_df, weighted_avg_outliers_score, weighted_avg_std_ping_time_score = average_variability_metrics(df,data)
        #print(results_df)
        #print(f"============== {i} component(s) ================")
        print(f"Weighted average of variability score when {i} component(s): ", weighted_avg_std_ping_time_score,f" Outlier score when {i} component(s): ", weighted_avg_outliers_score)

search_gmm_weighted_avg(df_mi,all_cleaned_df)

Weighted average of variability score when 2 component(s):  9.816217937602742  Outlier score when 2 component(s):  3.9305555555555554
Weighted average of variability score when 3 component(s):  33.43590126862295  Outlier score when 3 component(s):  8.50195509097948
Weighted average of variability score when 4 component(s):  29.499380613489773  Outlier score when 4 component(s):  9.77376622450435
Weighted average of variability score when 5 component(s):  64.15166568778453  Outlier score when 5 component(s):  10.700771043771045
Weighted average of variability score when 6 component(s):  37.4106623063501  Outlier score when 6 component(s):  9.999339426006093
Weighted average of variability score when 7 component(s):  41.17142914236316  Outlier score when 7 component(s):  8.63906816525864
Weighted average of variability score when 8 component(s):  364.72501135425426  Outlier score when 8 component(s):  10.684411736811786
Weighted average of variability score when 9 component(s):  305.2390

Based on the result we will be investigating the when n component is 7 and 11.

### Visual Investigate Clustering performance

In [98]:
def visualize_lineplot_ping_time_with_variability(df, target = []):
    """
    Visualize the effect of range on ping time for each delay separately with variability.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    """
    # Group by sensor ID, delay, and range, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Delay (us)', 'Range (cm)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    target_df = grouped_df[grouped_df['Sensor ID'].isin(target)]
    # Get unique delays
    unique_delays = target_df['Delay (us)'].unique()

    for delay in unique_delays:
        subset_df = target_df[target_df['Delay (us)'] == delay]

        fig = px.line(

        )

        # Adding error bars
        for sensor_id in subset_df['Sensor ID'].unique():
            sensor_data = subset_df[subset_df['Sensor ID'] == sensor_id]
            fig.add_trace(
                go.Scatter(
                    x=sensor_data['Range (cm)'],
                    y=sensor_data['mean_ping_time'],
                    mode='lines+markers',
                    name=f'Sensor {sensor_id}',
                    error_y=dict(
                        type='data',
                        array=sensor_data['std_ping_time'],
                        visible=True
                    )
                )
            )

        # Plot reference line
        ranges = np.linspace(subset_df['Range (cm)'].min(), subset_df['Range (cm)'].max(), 100)
        reference_ping_times = 57 * ranges
        fig.add_trace(
            go.Scatter(
                x=ranges,
                y=reference_ping_times,
                mode='lines',
                line=dict(color='red', dash='dash'),
                name='Reference Line'
            )
        )

        fig.update_layout(
            xaxis_title='Range (cm)',
            yaxis_title='Mean Ping Time (us)',
            legend_title='Sensor ID',
            template='plotly_white'
        )

        fig.show()

def visualize_lineplot_ping_time_with_variability_simple(df, target=[]):
    """
    Visualize the effect of range on ping time for each delay separately with variability.

    Parameters:
    df (DataFrame): The DataFrame containing the data.
    target (list): List of target sensor IDs to visualize.
    """
    # Group by sensor ID, delay, and range, then calculate the mean and standard deviation of ping time
    grouped_df = df.groupby(['Sensor ID', 'Delay (us)', 'Range (cm)']).agg(
        mean_ping_time=('Ping Time (us)', 'mean'),
        std_ping_time=('Ping Time (us)', 'std')
    ).reset_index()

    target_df = grouped_df[grouped_df['Sensor ID'].isin(target)]
    # Get unique delays
    unique_delays = target_df['Delay (us)'].unique()

    # Define the number of columns for subplots
    num_columns = 2  # 2 columns for the grid
    num_rows = 3  # 3 rows for the grid

    # Create subplots
    fig = make_subplots(rows=num_rows, cols=num_columns, subplot_titles=[f'Delay: {delay} us' for delay in unique_delays])

    for i, delay in enumerate(unique_delays):
        subset_df = target_df[target_df['Delay (us)'] == delay]

        # Get the row and column position for the subplot
        row = (i // num_columns) + 1
        col = (i % num_columns) + 1

        # Adding error bars
        for sensor_id in subset_df['Sensor ID'].unique():
            sensor_data = subset_df[subset_df['Sensor ID'] == sensor_id]
            fig.add_trace(
                go.Scatter(
                    x=sensor_data['Range (cm)'],
                    y=sensor_data['mean_ping_time'],
                    mode='lines+markers',
                    name=f'Sensor {sensor_id}',
                    error_y=dict(
                        type='data',
                        array=sensor_data['std_ping_time'],
                        visible=True
                    )
                ),
                row=row, col=col
            )

        # Plot reference line
        ranges = np.linspace(subset_df['Range (cm)'].min(), subset_df['Range (cm)'].max(), 100)
        reference_ping_times = 57 * ranges
        fig.add_trace(
            go.Scatter(
                x=ranges,
                y=reference_ping_times,
                mode='lines',
                line=dict(color='red', dash='dash'),
                name='Reference Line'
            ),
            row=row, col=col
        )

    fig.update_layout(
        height=1500,  # Adjust height for the grid layout
        width=1500,  # Adjust width for the grid layout
        showlegend=False,
        title_text="Ping Time vs Range for Different Delays"
    )

    fig.show()

def visualize_cluster(df,cluster = 0, simple = True):
    # Load the dataset
    file_path = '../processed_data/all_data_v4-1-1_cleaned_sensor211.csv'
    all_cleaned_df = pd.read_csv(file_path)
    all_cleaned_df = all_cleaned_df.drop("Unnamed: 0",axis=1)
    
    cluster_sensors = df[df["cluster"]==cluster]["Sensor ID"].unique()
    if simple:
        visualize_lineplot_ping_time_with_variability_simple(all_cleaned_df,cluster_sensors)
    else:
        visualize_lineplot_ping_time_with_variability(all_cleaned_df,cluster_sensors)
    

## Test df_mi 

### Investigate df_mi with n_components 7 

Training the model

In [99]:
df_mi_gmm_7,gmm_7 = train_GMM(df_mi, n_components=7, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0    56
1    98
2    13
3    25
4     1
5    16
6     1
Name: Sensor ID, dtype: int64
BIC: 2019.3547706175877
AIC: 195.1811663765676


In [40]:
search_gmm_weighted_avg(df_mi,all_cleaned_df)

Weighted average of variability score when 2 component(s):  9.816217937602742  Outlier score when 2 component(s):  3.9305555555555554
Weighted average of variability score when 3 component(s):  33.43590126862295  Outlier score when 3 component(s):  8.50195509097948
Weighted average of variability score when 4 component(s):  29.499380613489773  Outlier score when 4 component(s):  9.77376622450435
Weighted average of variability score when 5 component(s):  64.15166568778453  Outlier score when 5 component(s):  10.700771043771045
Weighted average of variability score when 6 component(s):  37.4106623063501  Outlier score when 6 component(s):  9.999339426006093
Weighted average of variability score when 7 component(s):  41.17142914236316  Outlier score when 7 component(s):  8.63906816525864
Weighted average of variability score when 8 component(s):  364.72501135425426  Outlier score when 8 component(s):  10.684411736811786
Weighted average of variability score when 9 component(s):  305.2390

In [41]:
results_df, weighted_avg_outliers_score, weighted_avg_std_ping_time_score = average_variability_metrics(df_mi_gmm_7,all_cleaned_df)

print(weighted_avg_outliers_score, weighted_avg_std_ping_time_score)
results_df

9.45483385661957 39.13950458686444


cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        5                 119           16.177778          20.468185     16   
1        2                 173           54.355556          38.731820     13   
2        1                 665          130.822222         102.385542     98   
3        0                 261           70.466667          22.074261     56   
4        3                 244           44.000000         498.787720     25   
5        6                  19            4.644444          13.420619      1   
6        4                  23            3.577778          16.225759      1   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     6.426389                    7.675569  
1                     9.126496                    8.938112  
2                     5.450794                    2.089501  
3                     3.402381                    0.394183  
4                     8.000000                   79.806035  
5                    14.355556                   93.944334  
6                    19.422222                   81.128797

#### Cluster 3: Majority cluster 



In [42]:
visualize_cluster(df_mi_gmm_7,3)

#### Cluster 0: another majority cluster

In [43]:
visualize_cluster(df_mi_gmm_7,0)

#### Cluster 2: decent sized cluster

In [45]:
visualize_cluster(df_mi_gmm_7,2)

From this visualziation it showed the potential where comparing the cluster 0 and 2's wehn delay 10000 cluster 0 seems to be cluster of over measuring and cluster 2 is under measuring 

Idea for feature engineering: we can have like a slope 


In [46]:
visualize_cluster(df_mi_gmm_7,1)

In [126]:
visualize_cluster(df_mi_gmm_7,5)

### Investigate df_mi with 11 n_components

Training the model

In [100]:
df_mi_gmm_11,gmm_11 = train_GMM(df_mi, n_components=11, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0     58
1     87
2     13
3     13
4      1
5      1
6     16
7     18
8      1
9      1
10     1
Name: Sensor ID, dtype: int64
BIC: 2561.5437305117816
AIC: -306.92742331308864


#### Cluster 3: majority cluster

In [50]:
visualize_cluster(df_mi_gmm_11,3)

#### Cluster 0: another majority cluster

In [51]:
visualize_cluster(df_mi_gmm_11,0)

#### Cluster 10: another majority cluster

In [ ]:
visualize_cluster(df_mi_gmm_11,10)

## Test df_mi_50

Training the model

In [52]:
best_gmm_model, tuning_results = tune_gmm(df_mi_50, n_components_range=range(1, 15), criterion='AIC')
print(best_gmm_model)

GaussianMixture(n_components=13, random_state=42)


Test n_component 10 and 13

In [53]:
search_gmm_weighted_avg(df_mi_50,all_cleaned_df)

Weighted average of variability score when 2 component(s):  6.525658107988389  Outlier score when 2 component(s):  7.371708319809586
Weighted average of variability score when 3 component(s):  5.427907692365612  Outlier score when 3 component(s):  7.605090339080934
Weighted average of variability score when 4 component(s):  9.226755473478963  Outlier score when 4 component(s):  7.127887025745258
Weighted average of variability score when 5 component(s):  37.34016607288425  Outlier score when 5 component(s):  6.8433738777720805
Weighted average of variability score when 6 component(s):  12.901021326333996  Outlier score when 6 component(s):  6.368737725318591
Weighted average of variability score when 7 component(s):  19.673693119419834  Outlier score when 7 component(s):  6.761227376048223
Weighted average of variability score when 8 component(s):  23.14252900000961  Outlier score when 8 component(s):  7.914120036342259
Weighted average of variability score when 9 component(s):  30.738

### Investigate df_mi_50 with 13 n_components

In [101]:
df_mi_50_gmm_13,mi_50_gmm_13 = train_GMM(df_mi_50, n_components=13, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0      9
1     18
2     34
3     13
4     18
5     10
6     22
7     34
8     12
9      1
10     3
11     1
12    35
Name: Sensor ID, dtype: int64
BIC: 37699.481229825506
AIC: -19994.611277151496


In [60]:
results_df, _,_ = average_variability_metrics(df_mi_50_gmm_13,all_cleaned_df)

results_df

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        11                 187           48.911111          22.425665     22   
1        12                 250           71.533333          44.642995     11   
2         8                  58           30.288889          26.009047     14   
3         0                 143           18.622222          14.504102     12   
4         4                 165           29.022222         136.252529     21   
5         3                  94           18.600000         234.767292     10   
6         5                 291           46.733333          71.415563     42   
7         2                 111           20.311111          59.173938     24   
8         6                 156           55.288889          11.747254     17   
9         7                 150           27.733333         161.713090     17   
10       10                  59            5.733333         605.100547      3   
11        1                 156           28.711111         541.794678     16   
12        9                  23            3.577778          16.225759      1   

    weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                      6.276768                   12.232181  
1                     16.224242                   52.759903  
2                      1.979365                   16.720102  
3                     10.364815                    1.208675  
4                      6.475132                   32.441078  
5                      7.540000                   93.906917  
6                      5.815873                   10.202223  
7                      3.778704                    7.396742  
8                      5.924183                    4.837105  
9                      7.192157                   76.100277  
10                    17.755556                 2218.702007  
11                     7.955556                   67.724335  
12                    19.422222                  162.257594

In [ ]:
#visualize_cluster(df_mi_50_gmm_13,1)

From this visualization we can see they are grouped where it trouble detecting at delay 16800 range 13.

## Test df_corr_scaled_mi_batch_50

Training the model

In [ ]:
best_gmm_model, tuning_results = tune_gmm(df_corr_scaled_mi_batch_50, n_components_range=range(1, 15), criterion='AIC')
print(best_gmm_model)

GaussianMixture(n_components=14, random_state=42)


In [62]:
search_gmm_weighted_avg(df_corr_scaled_mi_batch_50,all_cleaned_df)

Weighted average of variability score when 2 component(s):  5.646021899490217  Outlier score when 2 component(s):  6.8041338979633
Weighted average of variability score when 3 component(s):  6.306042138053255  Outlier score when 3 component(s):  7.143488200092352
Weighted average of variability score when 4 component(s):  6.3783610466039535  Outlier score when 4 component(s):  8.28623191802224
Weighted average of variability score when 5 component(s):  36.08830881375295  Outlier score when 5 component(s):  7.02294499062541
Weighted average of variability score when 6 component(s):  36.147365810988454  Outlier score when 6 component(s):  8.027664762550584
Weighted average of variability score when 7 component(s):  124.76944202286246  Outlier score when 7 component(s):  9.80185598277929
Weighted average of variability score when 8 component(s):  108.30502871252521  Outlier score when 8 component(s):  7.168141268034837
Weighted average of variability score when 9 component(s):  76.6863852

Test n_component 10 and 15 based on the score result

In [65]:
df_corr_scaled_mi_batch_50_gmm_10,mi_batch_gmm_10 = train_GMM(df_corr_scaled_mi_batch_50, n_components=10, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0    17
1    15
2    20
3    30
4    16
5    32
6    20
7    39
8    20
9     1
Name: Sensor ID, dtype: int64
BIC: 21002.94895061158
AIC: -25116.845715144416


In [70]:
results_df, _,_ = average_variability_metrics(df_corr_scaled_mi_batch_50_gmm_10,all_cleaned_df)

results_df

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        6                 149           22.444444          17.479789     20   
1        2                 314           44.822222          32.185802     20   
2        0                 143           32.511111          42.833711     17   
3        8                 165           24.333333         116.251328     20   
4        5                 245           41.644444         150.100719     32   
5        4                 110           29.422222          29.080173     16   
6        3                 201           34.822222         136.069175     30   
7        7                 219           35.400000          41.848902     39   
8        1                 158           34.244444         636.990687     15   
9        9                  23            3.577778          16.225759      1   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     6.327778                    6.117926  
1                    13.458889                    4.827870  
2                     6.499346                    2.519630  
3                     7.033333                   52.313098  
4                     6.354861                   28.143885  
5                     5.036111                    9.087554  
6                     5.539259                   18.142557  
7                     4.707692                    8.584390  
8                     8.250370                   84.932092  
9                    19.422222                  162.257594

#### cluster 9: outliers

First thing that I want to look into is Cluster 9 where it has a individual score of 102.
Lower is better but this may not be always true for all since some cluster is just cluster of outliers

In [71]:
visualize_cluster(df_corr_scaled_mi_batch_50_gmm_10,9)

as we can see this cluster is compose of outlier that have outgoing on 16800 range 13

#### Cluster 5: var score 12.607090

In [ ]:
visualize_cluster(df_corr_scaled_mi_batch_50_gmm_10,5)

Notice they all at range 13, 18, 33,and 38 have over measurement.

#### Cluter 7: majority cluster 

num: 31 score :19.081381

In [72]:
visualize_cluster(df_corr_scaled_mi_batch_50_gmm_10,7)

#### Cluster 0: with low score
0	44.284186	16	2.767762

In [ ]:
visualize_cluster(df_corr_scaled_mi_batch_50_gmm_10,0)

more of constant over measurment but there are some noticable outliers

## Test df_corr_scaled_mi_nofreq_50

Training the model

In [ ]:
best_gmm_model, tuning_results = tune_gmm(df_corr_scaled_mi_nofreq_50, n_components_range=range(1, 15), criterion='AIC')
print(best_gmm_model)

GaussianMixture(n_components=11, random_state=42)


In [63]:
search_gmm_weighted_avg(df_corr_scaled_mi_nofreq_50,all_cleaned_df)

Weighted average of variability score when 2 component(s):  5.872857816515448  Outlier score when 2 component(s):  7.427983056370154
Weighted average of variability score when 3 component(s):  12.369469635434788  Outlier score when 3 component(s):  8.179533091989233
Weighted average of variability score when 4 component(s):  7.67670116202259  Outlier score when 4 component(s):  7.44755924929759
Weighted average of variability score when 5 component(s):  30.107506113506947  Outlier score when 5 component(s):  8.22496065947236
Weighted average of variability score when 6 component(s):  46.83209578272121  Outlier score when 6 component(s):  9.9336934560921
Weighted average of variability score when 7 component(s):  42.899945989478624  Outlier score when 7 component(s):  9.991626416042498
Weighted average of variability score when 8 component(s):  96.5090683094375  Outlier score when 8 component(s):  7.621754623976846
Weighted average of variability score when 9 component(s):  26.458398161

Test n_component 10 and 15 based on the score result

Also test n_component = 9 and 16

### n_component = 10

In [77]:
df_nofreq_50_gmm_10,mi_nofreq_gmm_10 = train_GMM(df_corr_scaled_mi_nofreq_50, n_components=10, random_state=42, visualization_method='TSNE', plot_3d=False)

============ Distribution of Sensors in each Cluster ============
cluster
0    21
1    12
2    30
3    19
4     2
5    11
6    32
7     7
8    23
9    53
Name: Sensor ID, dtype: int64
BIC: 28566.950556542797
AIC: -15812.34819324012


In [75]:
results_df_nofreq, _,_ = average_variability_metrics(df_nofreq_50_gmm_10,all_cleaned_df)

results_df_nofreq

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        7                 144           12.911111          15.058382      7   
1        5                 250           71.533333          44.642995     11   
2        3                 193           35.133333         184.272358     19   
3        0                 137           33.088889          58.729098     21   
4        8                 169           33.622222         125.908644     23   
5        9                 364           59.733333          98.410244     53   
6        2                 266           60.644444          23.009316     30   
7        6                 251           77.844444          34.024154     32   
8        4                  25            1.866667         291.387642      2   
9        1                 102           18.333333         732.987400     12   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                    18.726984                   17.209580  
1                    16.224242                   24.350724  
2                     8.308772                   38.794181  
3                     4.948148                    2.796624  
4                     5.885990                   49.268600  
5                     5.740881                   18.567971  
6                     6.845185                    2.300932  
7                     5.411111                    7.442784  
8                    11.566667                  728.469106  
9                     6.972222                  122.164567

#### Cluter 2: majority cluster 

In [ ]:
target_cluster = 2
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
8        2           38.41839     13                    8.865782


#### Cluster 7: cluster of under measurement and outliers

In [76]:
target_cluster = 7
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        7                 144           12.911111          15.058382      7   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                    18.726984                    17.20958  


This cluster seems to be collection of under measurement and outliers

#### Cluster 6: over measurement and but with some outliers

In [ ]:
target_cluster = 6
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
6        6          19.326678     30                    4.509558


This cluster seems to be above measurement clusters

### Investigate other clusters 0,1,3,4,5,8,9

In [ ]:
target_cluster = 0
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
3        0          56.918241     27                    2.108083


Cluster 0 seems to be over measurements

In [ ]:
target_cluster = 1
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
9        1         644.854101     15                   85.980547


In [ ]:
target_cluster = 3
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
2        3         104.280144     24                   17.380024


In [ ]:
target_cluster = 4
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
1        4          57.759452     12                   24.066438


In [ ]:
target_cluster = 5
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
0        5          13.235223      6                   13.235223


In [ ]:
target_cluster = 8
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
7        8         115.289278     29                   35.779431


In [ ]:
target_cluster = 9
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_10,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
4        9         147.287194     20                   73.643597


### n_component = 15

In [110]:
df_nofreq_50_gmm_15,mi_nofreq_gmm_15 = train_GMM(df_corr_scaled_mi_nofreq_50, n_components=15, random_state=42,visualization_method='TSNE')

============ Distribution of Sensors in each Cluster ============
cluster
0     22
1     16
2     16
3     20
4     11
5      6
6     28
7     24
8     25
9     20
10     3
11    11
12     2
13     5
14     1
Name: Sensor ID, dtype: int64
BIC: 42384.48588140764
AIC: -29457.830157912103


In [68]:
results_df_nofreq,_,_ = average_variability_metrics(df_nofreq_50_gmm_15,all_cleaned_df)

results_df_nofreq

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0         5                 113           16.155556          13.235223      6   
1        11                 199           51.866667         112.674297     11   
2         1                 203           30.000000         273.269666     16   
3         0                 171           43.355556          39.083631     22   
4         9                 139           26.511111         128.691599     20   
5         7                  54           14.644444          46.137700     24   
6         6                 241           73.488889          19.436478     28   
7         4                 155           41.444444         181.491011     11   
8         8                 233           54.177778          95.226744     25   
9        10                  59            5.733333         605.100547      3   
10        2                 146           21.266667          34.382311     16   
11        3                 196           22.200000          87.485551     20   
12       13                  57            9.177778         726.798499      5   
13       12                  37            3.733333         834.365006      2   
14       14                  23            3.666667          29.022530      1   

    weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                     16.140741                   13.235223  
1                     13.375758                  122.917415  
2                     10.812500                   34.158708  
3                      5.802020                    1.776529  
4                      5.624444                   64.345800  
5                      1.639815                   15.379233  
6                      5.982540                    4.859120  
7                     10.323232                   82.495914  
8                      7.152889                   34.281628  
9                     17.755556                 2218.702007  
10                     7.795833                    6.446683  
11                     8.690000                   17.497110  
12                     9.564444                 2035.035797  
13                    16.633333                 5423.372542  
14                    19.333333                  435.337948

#### Cluter 0:low ping time score

In [ ]:
target_cluster = 0
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
3        0          39.083631     22                    1.776529


#### Cluter 14 and 3: compare aimilar count and similar ping time score

In [ ]:
target_cluster = 14
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

    cluster  avg_std_ping_time  count  ping_time_clustering_score
14       14           29.02253      1                  435.337948


In [ ]:
target_cluster = 3
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

    cluster  avg_std_ping_time  count  ping_time_clustering_score
11        3          87.485551     20                    17.49711


#### Cluter 2,6,and 5: compare majority cluster 

In [ ]:
target_cluster = 6
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
6        6          19.436478     28                     4.85912


In [ ]:
target_cluster = 5
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
0        5          13.235223      6                   13.235223


In [ ]:
target_cluster = 2
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

    cluster  avg_std_ping_time  count  ping_time_clustering_score
10        2          34.382311     16                    6.446683


As a result n_component 10 seems to be more promising so I will be investigating this further.

#### Investigate rest data points

In [ ]:
target_cluster = 1
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
2        1         273.269666     16                   34.158708


In [ ]:
target_cluster = 4
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
7        4         181.491011     11                   82.495914


In [ ]:
target_cluster = 7
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
5        7            46.1377     24                   15.379233


In [ ]:
target_cluster = 8
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_15,target_cluster)

   cluster  avg_std_ping_time  count  ping_time_clustering_score
8        8          95.226744     25                   34.281628


### Test n_component 9

In [64]:
df_nofreq_50_gmm_9,mi_nofreq_gmm_9 = train_GMM(df_corr_scaled_mi_nofreq_50, n_components=9, random_state=42)

============ Distribution of Sensors in each Clusters ============
cluster
0    26
1    17
2    21
3    23
4    11
5     8
6    33
7    39
8    32
Name: Sensor ID, dtype: int64
BIC: 18251.14954648754
AIC: -24852.901234092024


In [69]:
results_df_nofreq,_,_ = average_variability_metrics(df_nofreq_50_gmm_9,all_cleaned_df)

results_df_nofreq

cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
0        5                 157           16.111111          47.961859      8   
1        4                 250           71.533333          44.642995     11   
2        7                 174           40.155556          77.316320     39   
3        0                 173           54.933333          78.912091     26   
4        2                 158           28.555556          10.822923     21   
5        6                 279           85.755556          18.426374     33   
6        8                 274           61.311111         148.020920     32   
7        1                 163           36.222222         603.269812     17   
8        3                 200           22.044444         123.080830     23   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
0                    17.611111                   35.971394  
1                    16.224242                   20.292270  
2                     3.431909                   15.859758  
3                     4.541026                    3.035080  
4                     6.164021                    1.546132  
5                     5.855892                    3.908625  
6                     6.646528                   41.630884  
7                     7.457516                   70.972919  
8                     7.737198                   21.405362

#### Test major cluster 7 where it has low outlier score and moderate avg ping time score

In [83]:
target_cluster = 7
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_9,target_cluster)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
2        7                 174           40.155556           77.31632     39   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
2                     3.431909                   15.859758  


In [97]:
target_cluster = 0
print(results_df_nofreq[results_df_nofreq["cluster"]==target_cluster])
visualize_cluster(df_nofreq_50_gmm_9,target_cluster,simple=False)

   cluster  max_count_outliers  avg_count_outliers  avg_std_ping_time  count  \
3        0                 173           54.933333          78.912091     26   

   weighted_avg_count_outliers  weighted_avg_std_ping_time  
3                     4.541026                     3.03508  


# K-Means

In [ ]:
import numpy as np
import pandas as pd
from sklearn.preprocessing import StandardScaler
from sklearn.cluster import KMeans
import plotly.express as px
import plotly.graph_objs as go

def tune_and_visualize_kmeans(data, n_clusters_range=range(1, 11), plot_3d=False):
    """
    Perform hyperparameter tuning for KMeans clustering,
    store the results in a DataFrame, visualize the results, and return the best model.
    Optionally, create an interactive 3D plot of the clustering results.

    Parameters:
    - data: pd.DataFrame - The input data for KMeans clustering.
    - n_clusters_range: range - The range of number of clusters to try.
    - plot_3d: bool - Whether to create an interactive 3D plot of the clustering results.

    Returns:
    - best_model: KMeans - The best KMeans model based on the inertia criterion.
    - results_df: pd.DataFrame - The DataFrame containing inertia values for each model.
    """
    
    # Drop the target column if it's present
    if 'target' in data.columns:
        data = data.drop('target', axis=1)

    # Standardize the features
    scaler = StandardScaler()
    features_scaled = scaler.fit_transform(data)

    # Create lists to store the results
    inertia_values = []
    n_clusters_list = []

    # Loop over the range of clusters
    for n_clusters in n_clusters_range:
        kmeans = KMeans(n_clusters=n_clusters, n_init='auto',random_state=42)
        kmeans.fit(features_scaled)
        
        inertia = kmeans.inertia_
        
        inertia_values.append(inertia)
        n_clusters_list.append(n_clusters)

    # Create a DataFrame to store the results
    results_df = pd.DataFrame({
        'n_clusters': n_clusters_list,
        'Inertia': inertia_values
    })

    # Plot the inertia values
    fig = px.line(results_df, x='n_clusters', y='Inertia', 
                  title='Inertia values for different number of clusters',
                  labels={'Inertia': 'Inertia', 'n_clusters': 'Number of Clusters'},
                  markers=True)
    fig.show()

    # Find the best model based on the inertia (elbow method)
    best_index = results_df['Inertia'].idxmin()
    best_n_clusters = results_df.loc[best_index, 'n_clusters']
    best_model = KMeans(n_clusters=best_n_clusters, random_state=42)
    best_model.fit(features_scaled)

    # Optionally, create an interactive 3D plot of the clustering results
    if plot_3d:
        if features_scaled.shape[1] < 3:
            raise ValueError("The dataset must have at least 3 features for a 3D plot.")
        
        # Predict cluster labels
        cluster_labels = best_model.predict(features_scaled)
        data['cluster'] = cluster_labels
        
        # Create 3D scatter plot
        fig_3d = px.scatter_3d(
            data, 
            x=features_scaled[:, 0], 
            y=features_scaled[:, 1], 
            z=features_scaled[:, 2], 
            color='cluster',
            title='KMeans Clustering Results in 3D',
            labels={'x': 'Feature 1', 'y': 'Feature 2', 'z': 'Feature 3'}
        )
        fig_3d.show()

    return best_model, results_df


In [ ]:
def train_KMeans(df, n_clusters=5, random_state=42):
    # Standardize the features
    scaler = StandardScaler()
    features_scaled = scaler.fit_transform(df)

    # Fit a KMeans model
    kmeans = KMeans(n_clusters=n_clusters, random_state=random_state,n_init='auto')
    kmeans.fit(features_scaled)

    # Predict cluster labels
    cluster_labels = kmeans.predict(features_scaled)
    df['cluster'] = cluster_labels

    # Evaluate the model using inertia
    inertia = kmeans.inertia_

    print(f"Inertia: {inertia}")

    return df, kmeans



In [ ]:
def search_kmeans_weighted_avg(df,data, n_components_range=range(2, 20)):
    for i in n_components_range:
        # Standardize the features
        scaler = StandardScaler()
        features_scaled = scaler.fit_transform(df)

        # Fit a KMeans model
        kmeans = KMeans(n_clusters=i, n_init='auto', random_state=42)
        kmeans.fit(features_scaled)


        # Predict cluster labels
        cluster_labels = kmeans.predict(features_scaled)
        df['cluster'] = cluster_labels
        
        results_df, weighted_average = average_variability_index(df,data)
        #print(results_df)
        print(f"Weighted average of variability score when {i} component(s): ", weighted_average)


In [ ]:
best_kmeans_model, tuning_results = tune_and_visualize_kmeans(df_corr_scaled_mi_nofreq_50, n_clusters_range=range(1, 30), plot_3d=False)
print(best_kmeans_model)

KMeans(n_clusters=29, random_state=42)


/Users/jihoonchung/anaconda3/envs/datascience/lib/python3.10/site-packages/sklearn/cluster/_kmeans.py:1412: FutureWarning:

The default value of `n_init` will change from 10 to 'auto' in 1.4. Set the value of `n_init` explicitly to suppress the warning



In [ ]:
search_kmeans_weighted_avg(df_corr_scaled_mi_nofreq_50,all_cleaned_df)

Weighted average of variability score when 2 component(s):  1.9036060271759543
Weighted average of variability score when 3 component(s):  12.786015843241428
Weighted average of variability score when 4 component(s):  4.972202375437147
Weighted average of variability score when 5 component(s):  14.740899383642574
Weighted average of variability score when 6 component(s):  48.49335213949448
Weighted average of variability score when 7 component(s):  45.30533442787829
Weighted average of variability score when 8 component(s):  23.74409073692469
Weighted average of variability score when 9 component(s):  38.04590277169384
Weighted average of variability score when 10 component(s):  77.68281568372802
Weighted average of variability score when 11 component(s):  312.379443302562
Weighted average of variability score when 12 component(s):  274.37417030849724
Weighted average of variability score when 13 component(s):  565.4163382948384
Weighted average of variability score when 14 component(s

In [ ]:
nofreq_clustered_data, kmeans_model = train_KMeans(df_corr_scaled_mi_nofreq_50, n_clusters=15, random_state=42)

Inertia: 6986.806277803522


In [ ]:
results_df, ping_time_clustering_score = average_variability_index(nofreq_clustered_data,all_cleaned_df)

print(ping_time_clustering_score)
results_df

299.5927722065857


cluster  avg_std_ping_time  count  ping_time_clustering_score
0        12           9.659042     11                   11.415231
1         8          45.465384     10                   40.918846
2         1         134.493948     25                   10.759516
3        10          35.424603     22                   17.712301
4         4         159.293516     16                   49.779224
5        11          79.476094     21                   45.414911
6         2          20.432087     25                    2.451850
7         3         147.110643     24                   24.518441
8         7         134.712025     22                   48.986191
9        14         678.746779     11                  925.563790
10        0          40.487251     19                    2.130908
11        5          13.420619      1                   80.523715
12        6         380.734807      1                 2665.143647
13       13          29.022530      1                  406.315418
14        9          16.225759      1                  162.257594

In [ ]:
visualize_cluster(nofreq_clustered_data,0)

In [ ]:
visualize_cluster(nofreq_clustered_data,2)